
## Title translation and similarity comparison (evaluation)<br>

In the following, we translate the titles using Google Translate API (find documentation at [googletrans 4.0.0rc1](https://pypi.org/project/googletrans/4.0.0rc1/) ). After that, we embed them using a pre-trained language model (**BERT**) and apply **cosine similarity** to give a first human readable score of title similarity.


### Important remarks on Google Translate API

As can be read in the documentation, this API has several critical restriction for its use which we list below: <br><br>

1. The maximum character limit for translation of a single text is 15k  
2. The number of files that can be translated in a single session is highly variable. In our experience, it is between 1 and 5000 files. 
3. The API can easily ban the user's client IP address for a variable time (several hours usually) as a consequence of a great usage of the service. This might also depend on how many translations are done per unit of time, this means that sometimes the execution of programs has been artificially stopped or delayed (e.g. with `time.sleep()`).
4. The API depends on the status and stability of the web version of Google Translate

In [5]:
import os
from bs4 import BeautifulSoup
import json
from googletrans import Translator # pip install googletrans==4.0.0-rc1

import pandas as pd
import numpy as np

from sklearn.metrics.pairwise import cosine_similarity
from sentence_transformers import SentenceTransformer # pip install sentence_transformers

translator = Translator()

model = SentenceTransformer('bert-base-nli-mean-tokens') 

In [6]:
eval_df = pd.read_csv ('eval/_EVAL_details_in_df.csv')
title_df = pd.DataFrame(columns = ["pair_id","url1_lang", "google_lang1","url2_lang","google_lang2", "title1","title2","translated_title1","translated_title2"])
eval_df

pair_id url1_lang url2_lang  \
0     1484189203_1484121193        en        en   
1     1484011097_1484011106        en        en   
2     1484039488_1484261803        en        en   
3     1484332324_1484796748        en        en   
4     1484012256_1484419682        en        en   
...                     ...       ...       ...   
4897  1553907621_1553488848        es        it   
4898  1646957948_1643667075        es        it   
4899  1504063453_1502866628        es        it   
4900  1647862428_1647712939        es        it   
4901  1636570015_1637492652        es        it   

                                                 title1  \
0        Police: 2 men stole tools from Lowe’s in Davie   
1     Open database leaked 179GB in customer, US gov...   
2     Ducks are own worst enemies in sloppy loss in ...   
3     Another Bengal vs Centre tussle? Govt rejects ...   
4     Bars and clubs you loved and lost this decade ...   
...                                                 ...   
4897  Denver Nuggets reporta que “un miembro de la o...   
4898  Vivir en España es más barato que en la media ...   
4899  Activan sistema de vigilancia epidemiológica e...   
4900  Emite Irán orden de arresto contra Tump por as...   
4901  Biden, con más de 10 puntos que Trump en estad...   

                                                 title2  \
0      No-swim advisory lifted for Deerfield Beach Pier   
1     Best Western’s Massive Data Leak: 179GB Amazon...   
2     Woody Guthrie's 1943 New Year's Resolutions ar...   
3     'Congress Rejected 7 Times': BJP's Reminder as...   
4                             Top 20 films of the 2010s   
...                                                 ...   
4897    Coronavirus, un caso anche fra i Denver Nuggets   
4898  Coronavirus, in Europa 140mila morti in più in...   
4899  Coronavirus in Cina: consumo di serpenti e zup...   
4900  Iran emette mandato di arresto per Trump per l...   
4901  Sondaggio Usa 2020: Biden in vantaggio nei 6 S...   

                                              keywords1  \
0                        More Trending Stories,Trending   
1     AI,Hardware,Executive Guides,Cloud,Microsoft,S...   
2                                         anaheim-ducks   
3     bengal latest news,mamata banrjee,republicday,...   
4     Broad Street Birmingham,ThingsToDoInBirmingham...   
...                                                 ...   
4897                                         Denver,NBA   
4898                                           EUROSTAT   
4899           vigilancia epidemiológica,ticker,puertos   
4900  ESTADOS UNIDOS,ESTADOSUNIDOS,DONALDTRUMP,IRÁN,...   
4901                                                NaN   

                                              keywords2  \
0                        More Trending Stories,Trending   
1     Best Western,Information Security,Privacy,aws,...   
2     keep the hope machine running,new year's resol...   
3     tableaux,WestBengal,Mamata Banerjee,West Benga...   
4     Marvel Cinematic Universe,People's Struggles,a...   
...                                                 ...   
4897  DenverNuggets,coronavirus,Denver Nuggets,Coron...   
4898                                             Estero   
4899                                           serpenti   
4900  corpodelleguardie,magistratura,iran,qasemsolei...   
4901                       JoeBiden,DonaldTrump,NewYork   

                                                  text1  \
0     DAVIE, FLA. (WSVN) - Police need help catching...   
1     Govt officials confirm Trump can block US comp...   
2     Ducks defenseman Erik Gudbranson, left, knocks...   
3     The West Bengal government’s proposal was reje...   
4     The video will start in 8 Cancel\n\nSign up to...   
...                                                 ...   
4897  Los Denver Nuggets de la NBA reportaron este j...   
4898  El estudio realizado por Eurostat muestra que ...   
4899  Foto: Archivo Foto: Archivo\n\nEl 


### Title translation

In what follows, we translate to English the title entries that are in a different language. Then, we compare the annotated language `url1_lang` and `url2_lang` with the languages detected by the automatic *source language* function of the Google Translate API (`.src`). <br><br>

The limitations of the Google Translate API have been avoided by dividing the titles into batches.

In [26]:
# we had to translate titles in batches, else googletran API will have a runtime error
i = 2632
j = i+3
(start,finish) = (i,j)

for index, row in eval_df.iterrows():  
    if index < start or index >= finish:
        continue
    
    if pd.isnull(row["title1"]) or pd.isnull(row["title2"]):
        continue
    
    if row["title1"]=='Wyborcza.pl' or row["title2"]=='Wyborcza.pl':
        continue
        
    result1 = translator.translate(row["title1"])
    translated1 =  result1.text
    lang1 = result1.src
    
    result2 = translator.translate(row["title2"])
    translated2 =  result2.text
    lang2 = result2.src
    print('---------------------',index,'-----------------------')
    print(row['pair_id'])
    print(row['title1'])
    print(row['url1_lang'],' ; ',lang1)
    print(translated1)
    print(row['title2'])
    print(row['url2_lang'],' ; ',lang2)
    print(translated2)
        
    entry = {"pair_id":row['pair_id'],"url1_lang":row['url1_lang'],"google_lang1":lang1,"url2_lang":row['url2_lang'],"google_lang2":lang2,"title1":row["title1"],"title2":row["title2"],"translated_title1":translated1,"translated_title2":translated2}
#     title_df = title_df.append(entry, ignore_index = True)
    


--------------------- 2632 -----------------------
1491699974_1491843728
"Niebezpieczne i prowokacyjne" zbliżenie rosyjskiego okrętu. US Navy pokazuje nagranie
pl  ;  pl
"Dangerous and provocative" closeup of the Russian ship.US Navy shows the recording
"Niebezpieczne i prowokacyjne". Kolejna agresja ze strony Rosji
pl  ;  pl
"Dangerous and provocative".Another aggression from Russia
--------------------- 2634 -----------------------
1558738653_1589907678
Koronawirus w Polsce. Tomasz Grodzki: "Za tydzień pilne posiedzenie Senatu"
pl  ;  pl
Coronavirus in Poland.Tomasz Grodzki: "Urgent Senate meeting for a week"
Tomasz Grodzki: Dyskutowany jest pomysł zmiany marszałka Sejmu
pl  ;  pl
Tomasz Grodzki: The idea of changing the Sejm marshal is discussed


In [28]:
# we found that because there are some nan or untranslatable titles, our title_df was smaller than eval_df, and the 
# index and pair_id don't matc, so we look into how to fix it

for index, row in eval_df.iterrows(): 
    if row['pair_id'] != title_df.iloc[index]['pair_id']:
        print('--------------',index,'--------------')
        print(row["title1"])
        print(row["title2"])
        print(row['pair_id'],title_df.iloc[index]['pair_id'])

-------------- 2633 --------------
Raport koronawirusa: Najwięcej zakażeń na Śląsku [MAPA]
nan
1615462021_1614797257 1558738653_1589907678
-------------- 2634 --------------
Koronawirus w Polsce. Tomasz Grodzki: "Za tydzień pilne posiedzenie Senatu"
Tomasz Grodzki: Dyskutowany jest pomysł zmiany marszałka Sejmu
1558738653_1589907678 1529968140_1529587446
-------------- 2635 --------------
Polska może opuścić UE? Tusk: Nie sądzę
Donald Tusk: mamy do czynienia ze swoistym rozpadem świata
1529968140_1529587446 1626177753_1626600561
-------------- 2636 --------------
Polska Press Sp. z o.o.
Matura 2020. Najczęściej wybierane przedmioty. Kiedy pierwszy egzamin?
1626177753_1626600561 1606494901_1570229246
-------------- 2637 --------------
Kolejny kraj po Polsce zgłasza problemy z maseczkami z UE
KE przypomina: Prawa pasażerów są chronione przez prawo w UE
1606494901_1570229246 1508960398_1510066669
-------------- 2638 --------------
Życie malutkiego wcześniaka zawisło na włosku. Lekarz włoż

1624178459_1554885289 1535806799_1600521076
-------------- 2829 --------------
В Казани начали возводить новый корпус инфекционной больницы
В Татарии выдано более 1 млн смс-разрешений для выхода из дома
1592131729_1572053422 1621124980_1621555894
-------------- 2830 --------------
Subaru открыла новый автоцентр в Набережных Челнах
Жителя Татарии обязали вернуть компенсацию за падение глыбы льда на машину
1619093586_1490481657 1568051061_1512431682
-------------- 2831 --------------
В Пермском крае возбудили дело против женщины, оставившей пятерых детей одних дома
В Пермском крае будут судить мать, бросившую пятерых детей в опасности
1645339568_1645353301 1514489958_1532711600
-------------- 2832 --------------
Главный санврач Узбекистана сделал заявление в связи с обнаружением коронавируса в стране
Первый случай коронавируса зарегистрирован в Узбекистане
1548604467_1548571990 1634649050_1615395313
-------------- 2833 --------------
Китай стимулирует импорт зерновых и лекарственного сыр

-------------- 3013 --------------
İngiliz vekil yeni tip koronavirüs sebebiyle kendini tecrit etti
Sonradan ortaya Ã§Ä±ktÄ±! Ä°ngiliz milletvekili koronavirÃ¼s nedeniyle kendini tecrit etti
1521337187_1521308356 1634748191_1634797540
-------------- 3014 --------------
Süper Lig: Denizlispor: 1Beşiktaş: 5 (Maç sonucu)
Beşiktaş maçı saat kaçta?
1640400754_1640040014 1572866753_1572867654
-------------- 3015 --------------
Mersin'de tarihi eser operasyonu: 2 gözaltı
Mersin'de 746 parça tarihi eser ele geçirildi
1489321289_1491371886 1631168105_1585554415
-------------- 3016 --------------
Merhamet hepimize lazımdır
Avrupalı liderlerin açıklamaları panik havasını artırıyor
1569112680_1551882430 1577854448_1578342689
-------------- 3017 --------------
Diyanet İşleri Başkanı Ali Erbaş: 29 Mayıs'ta camilerimize kavuşacağız, hasret bitecek
Diyanet İşleri Başkanı Erbaş: 'Ne yaptık da Rabbimiz insanlığa bu musibeti verdi' diyoruz
1611286118_1587701904 1634028441_1634047250
-------------- 3018 -

-------------- 3200 --------------
4月份主要指标显示 中国经济持续呈现积极变化
经济延续恢复改善势头（经济新方位）--财经--人民网
1608359666_1608184907 1603902969_1563803071
-------------- 3201 --------------
促进实物消费和服务消费回补（新知新觉）--财经--人民网
以辩证思维统筹疫情防控和经济社会发展（人民要论）--财经--人民网
1551355603_1537811567 1574260387_1613664708
-------------- 3202 --------------
精彩！“文化和自然遗产日”河南主场活动在洛阳举行
河南省“文化和自然遗产日”主题活动将在洛阳举办
1634280264_1632690669 1602894115_1602193464
-------------- 3203 --------------
香港证监会行政总裁再度获任国际证监会组织理事会主席--财经--人民网
香港金管局：资金流入港元显示市场对香港具有信心--财经--人民网
1631510593_1632620921 1521759971_1502982859
-------------- 3204 --------------
专访香港特区政府律政司前刑事检控专员江乐士：国家安全立法合法且必要！
大湾区之声热评：惩治“港独”“黑暴”，保护绝大多数
1621470844_1615888322 1636020820_1639926491
-------------- 3205 --------------
平江点对点发力源头治超
雨湖高新区召开“奋战一百天实现双过半＂竞赛活动动员会
1603902969_1563803071 1533819124_1531148592
-------------- 3206 --------------
洛阳年内将基本建成安全生产双重预防体系
我市印发《2020年洛阳市以案促改工作实施意见》
1574260387_1613664708 1584173636_1583602519
-------------- 3207 --------------
动态监测促整改--时政--人民网
一封信背后的深调研（代表委员履职故事）-

-------------- 3390 --------------
住建部：推进工程建设行业专项整治工作 回应人民关切--财经--人民网
两部门：对普惠性幼儿园不普惠等假治理行为加大问责力度--财经--人民网
1642103175_1590397703 1543248531_1543311697
-------------- 3391 --------------
巫统迎战2独立人士！珍尼补选掀三角战
疫情未完担心选民安全！希盟弃战珍尼州席补选
1639873446_1627261065 1490287331_1502214764
-------------- 3392 --------------
武汉人日记｜医护家属为战疫前线送爱心餐_纪录湃_澎湃新闻-The Paper
各地乐迷办云音乐节，喊话“朋克武汉”_纪录湃_澎湃新闻-The Paper
1543248531_1543311697 1584251217_1564162242
-------------- 3393 --------------
云南省深化纪检监察体制改革 健全和完善监督体系
省纪委监委多种方式开展《生物多样性公约》第十五次缔约方大会云南筹备工作专项纪律监督
1490287331_1502214764 1635951895_1635846323
-------------- 3394 --------------
菜鸟增开深圳-以色列出口航线 启动“客机改货机”
菜鸟开通杭州首条到吉隆坡货运航线 还将进一步扩大常态化包机
1584251217_1564162242 1556173446_1553726409
-------------- 3395 --------------
未披露同外国特别是中共关系 54名科学家从美国卫生研究院离职
未披露外国关系 54名美国科学家离职
1635951895_1635846323 1620761395_1529797167
-------------- 3396 --------------
信托资产规模降至21.6万亿 结构优化趋势明显
苹果中国官网开启限购，iPhone系列每人最多买两部
1556173446_1553726409 1490222701_1601768877
-------------- 3397 --------------
云

...

-------------- 4334 --------------
تعاونية الاتحاد توزع 24% أرباحا نقدية و6%عائدا على مشتريات المساهمين
«تعاونية الاتحاد» توزع 24% أرباحاً نقدية عن 2019
1565616507_1565961276 1562456621_1562263282
-------------- 4335 --------------
تركيا وروسيا يبدآن تسيير دورية عسكرية على طريق حلب اللاذقية
هل تؤدي الاستفزازات التركية بسوريا الى معركة شاملة
1599696930_1603920940 1628074548_1628217024
-------------- 4336 --------------
اختيار مدرستين بكل إدارة تعليمية بدمياط لتسليم شريحة التابلت لمنع التزاحم
زحام أمام سنترالات دمياط للحصول على شريحة تابلت التعليم ودفع الفواتير.. صور
1562456621_1562263282 1576002523_1574477350
-------------- 4337 --------------
ارتفاع مؤشرات بورصة الكويت بالمستهل وسط صعود جماعى للقطاعات
صعود جماعي بمؤشرات بورصة الكويت في ختام تعاملات اليوم
1628074548_1628217024 1608370577_1604200377
-------------- 4338 --------------
رئيس أوكرانيا عن محنة كورونا: تعبنا لكن لن نستسلم
أوكرانيا تطلب مستلزمات طبية من كوريا الجنوبية لمواجهة كورونا
1576002523_1574477350 1536038852_1536039807
-

Governor Cuomo, Governor Murphy, Governor Lamont, Governor Carney Announce Multi-state Agreement on Beaches Ahead of Memorial Day Weekend
North Country beaches to reopen May 22
1625832093_1607981162 1569776830_1569662245
-------------- 4530 --------------
A Middle East Stripped of Its Frills
President Trump Unveils 2 State Solution Peace Plan for the Middle East
1511910887_1578498460 1555339745_1626941722
-------------- 4531 --------------
Hector woman charged in shooting death of her boyfriend
Did he taunt his killer? Renville County man allegedly shot by girlfriend is ID'd
1569776830_1569662245 1592160843_1591967730
-------------- 4532 --------------
12 more corona-positive cases in Kerala, total count 49 #47806
12 more test positive in Kerala, total cases touch 49 – Democratic Accent
1555339745_1626941722 1502463250_1505469635
-------------- 4533 --------------
Turkey vows solidarity with US in fighting Covid-19 outbreak
Turkey donates masks and other equipment to US
1592160843_1591

1568367755_1568525300 1577371548_1577847928
-------------- 4705 --------------
Primer caso de coronavirus en Paraguay
El gobierno de Paraguay confirmó el primer caso en ese país
1542361308_1542148175 1619408581_1618666170
-------------- 4706 --------------
Jalisco pierde seis mil empleos en marzo
Jalisco pierde seis mil 026 puestos de trabajo en marzo
1577371548_1577847928 1581185514_1581777471
-------------- 4707 --------------
Ecuador registra 3.313 fallecidos oficiales y 38.471 positivos por COVID-19
Ecuador suma casi 500 nuevos casos de coronavirus y ya supera los 38.000 positivos
1619408581_1618666170 1622461532_1620336930
-------------- 4708 --------------
Guía para pagar servicios en locales de cobranza extrabancaria durante la cuarentena
Los locales de cobro de servicios podrán abrir desde el lunes
1581185514_1581777471 1586158751_1586105511
-------------- 4709 --------------
Simón critica los macrobotellones y recalca que esto no es un "sálvese quien pueda"
Sanidad informa de 

Denver Nuggets reporta que “un miembro de la organización” contrajo coronavirus
Coronavirus, un caso anche fra i Denver Nuggets
1553907621_1553488848 1504063453_1502866628
-------------- 4898 --------------
Vivir en España es más barato que en la media europea
Coronavirus, in Europa 140mila morti in più in marzo-aprile
1646957948_1643667075 1647862428_1647712939
-------------- 4899 --------------
Activan sistema de vigilancia epidemiológica en puertos y aeropuertos venezolanos – El Aragueño
Coronavirus in Cina: consumo di serpenti e zuppa di pipistrello tra le cause di trasmissione
1504063453_1502866628 1636570015_1637492652


IndexError: single positional indexer is out-of-bounds

In [59]:
# and decided to create new_title_df to store the entries correctly and have the untranslatble entries store ' ' as translated titles
new_title_df = pd.DataFrame(columns = ["pair_id","url1_lang", "google_lang1","url2_lang","google_lang2", "title1","title2","translated_title1","translated_title2"])


In [60]:

for i, row in eval_df.iterrows():
    entry = {}
    if row['pair_id'] == '1615462021_1614797257':
        result1 = translator.translate(row["title1"])
        translated1 =  result1.text
        entry = {"pair_id":row['pair_id'],"url1_lang":row['url1_lang'],"google_lang1":'pl',"url2_lang":row['url2_lang'],"google_lang2":'pl',"title1":row["title1"],"title2":row["title2"],"translated_title1":translated1,"translated_title2":' '}
    elif row['pair_id'] == '1556817289_1583857471':
        result2 = translator.translate(row["title2"])
        translated2 =  result2.text
        entry = {"pair_id":row['pair_id'],"url1_lang":row['url1_lang'],"google_lang1":'pl',"url2_lang":row['url2_lang'],"google_lang2":'pl',"title1":row["title1"],"title2":row["title2"],"translated_title1":' ',"translated_title2":translated2}
    
    elif row['pair_id'] == '1503683554_1606099875':
        result2 = translator.translate(row["title2"])
        translated2 =  result2.text
        entry = {"pair_id":row['pair_id'],"url1_lang":row['url1_lang'],"google_lang1":'pl',"url2_lang":row['url2_lang'],"google_lang2":'pl',"title1":row["title1"],"title2":row["title2"],"translated_title1":' ',"translated_title2":translated2}
    elif row['pair_id'] == '1556028980_1495786562':
        result2 = translator.translate(row["title2"])
        translated2 =  result2.text
        entry = {"pair_id":row['pair_id'],"url1_lang":row['url1_lang'],"google_lang1":'pl',"url2_lang":row['url2_lang'],"google_lang2":'pl',"title1":row["title1"],"title2":row["title2"],"translated_title1":' ',"translated_title2":translated2}
    elif row['pair_id'] == '1562291204_1561817442':
        result2 = translator.translate(row["title2"])
        translated2 =  result2.text
        entry = {"pair_id":row['pair_id'],"url1_lang":row['url1_lang'],"google_lang1":'pl',"url2_lang":row['url2_lang'],"google_lang2":'pl',"title1":row["title1"],"title2":row["title2"],"translated_title1":' ',"translated_title2":translated2}
    
    
    elif i < 4900 and row['pair_id']==title_df.iloc[i]['pair_id']:
        entry = {"pair_id":row['pair_id'],"url1_lang":row['url1_lang'],"google_lang1":title_df.iloc[i]["google_lang1"],"url2_lang":row['url2_lang'],"google_lang2":title_df.iloc[i]["google_lang2"],"title1":row["title1"],"title2":row["title2"],"translated_title1":title_df.iloc[i]["translated_title1"],"translated_title2":title_df.iloc[i]["translated_title2"]}
        
    elif i-1 < 4900 and row['pair_id']==title_df.iloc[i-1]['pair_id']:
        entry = {"pair_id":row['pair_id'],"url1_lang":row['url1_lang'],"google_lang1":title_df.iloc[i-1]["google_lang1"],"url2_lang":row['url2_lang'],"google_lang2":title_df.iloc[i-1]["google_lang2"],"title1":row["title1"],"title2":row["title2"],"translated_title1":title_df.iloc[i-1]["translated_title1"],"translated_title2":title_df.iloc[i-1]["translated_title2"]}
    elif i-2 < 4900 and row['pair_id']==title_df.iloc[i-2]['pair_id']:
        entry = {"pair_id":row['pair_id'],"url1_lang":row['url1_lang'],"google_lang1":title_df.iloc[i-2]["google_lang1"],"url2_lang":row['url2_lang'],"google_lang2":title_df.iloc[i-2]["google_lang2"],"title1":row["title1"],"title2":row["title2"],"translated_title1":title_df.iloc[i-2]["translated_title1"],"translated_title2":title_df.iloc[i-2]["translated_title2"]}
    elif i-3 < 4900 and row['pair_id']==title_df.iloc[i-3]['pair_id']:
        entry = {"pair_id":row['pair_id'],"url1_lang":row['url1_lang'],"google_lang1":title_df.iloc[i-3]["google_lang1"],"url2_lang":row['url2_lang'],"google_lang2":title_df.iloc[i-3]["google_lang2"],"title1":row["title1"],"title2":row["title2"],"translated_title1":title_df.iloc[i-3]["translated_title1"],"translated_title2":title_df.iloc[i-3]["translated_title2"]}
    elif i-4 < 4900 and row['pair_id']==title_df.iloc[i-4]['pair_id']:
        entry = {"pair_id":row['pair_id'],"url1_lang":row['url1_lang'],"google_lang1":title_df.iloc[i-4]["google_lang1"],"url2_lang":row['url2_lang'],"google_lang2":title_df.iloc[i-4]["google_lang2"],"title1":row["title1"],"title2":row["title2"],"translated_title1":title_df.iloc[i-4]["translated_title1"],"translated_title2":title_df.iloc[i-4]["translated_title2"]}
    elif i-5 < 4900 and row['pair_id']==title_df.iloc[i-5]['pair_id']:
        entry = {"pair_id":row['pair_id'],"url1_lang":row['url1_lang'],"google_lang1":title_df.iloc[i-5]["google_lang1"],"url2_lang":row['url2_lang'],"google_lang2":title_df.iloc[i-5]["google_lang2"],"title1":row["title1"],"title2":row["title2"],"translated_title1":title_df.iloc[i-5]["translated_title1"],"translated_title2":title_df.iloc[i-5]["translated_title2"]}
                       
    print('--------------',i,'--------------')
    print(entry)
    new_title_df = new_title_df.append(entry, ignore_index = True)


-------------- 0 --------------
{'pair_id': '1484189203_1484121193', 'url1_lang': 'en', 'google_lang1': 'en', 'url2_lang': 'en', 'google_lang2': 'en', 'title1': 'Police: 2 men stole tools from Lowe’s in Davie', 'title2': 'No-swim advisory lifted for Deerfield Beach Pier', 'translated_title1': 'Police: 2 men stole tools from Lowe’s in Davie', 'translated_title2': 'No-swim advisory lifted for Deerfield Beach Pier'}
-------------- 1 --------------
{'pair_id': '1484011097_1484011106', 'url1_lang': 'en', 'google_lang1': 'en', 'url2_lang': 'en', 'google_lang2': 'en', 'title1': 'Open database leaked 179GB in customer, US government, and military records', 'title2': 'Best Western’s Massive Data Leak: 179GB Amazon Database Open to All', 'translated_title1': 'Open database leaked 179GB in customer, US government, and military records', 'translated_title2': 'Best Western’s Massive Data Leak: 179GB Amazon Database Open to All'}
-------------- 2 --------------
{'pair_id': '1484039488_1484261803', '

C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat in

-------------- 9 --------------
{'pair_id': '1484188851_1483820477', 'url1_lang': 'en', 'google_lang1': 'en', 'url2_lang': 'en', 'google_lang2': 'en', 'title1': 'Over 1,700 Irish citizens required DFA assistance overseas in 2019', 'title2': 'Our 2020 Vision:', 'translated_title1': 'Over 1,700 Irish citizens required DFA assistance overseas in 2019', 'translated_title2': 'Our 2020 Vision:'}
-------------- 10 --------------
{'pair_id': '1484188282_1484590384', 'url1_lang': 'en', 'google_lang1': 'en', 'url2_lang': 'en', 'google_lang2': 'en', 'title1': 'The 10 best iPhone and iPad games of 2019', 'title2': 'Self Destructive Bastards', 'translated_title1': 'The 10 best iPhone and iPad games of 2019', 'translated_title2': 'Self Destructive Bastards'}
-------------- 11 --------------
{'pair_id': '1484188158_1483926746', 'url1_lang': 'en', 'google_lang1': 'en', 'url2_lang': 'en', 'google_lang2': 'en', 'title1': 'Holly Willoughby posts cryptic message to start off the new year', 'title2': 'Amer

C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat in

-------------- 17 --------------
{'pair_id': '1483737640_1484326372', 'url1_lang': 'en', 'google_lang1': 'en', 'url2_lang': 'en', 'google_lang2': 'en', 'title1': '10 things you should never do when starting a new job', 'title2': "New Year, New Resolution-Tips to Help Achieve This Year's Goal", 'translated_title1': '10 things you should never do when starting a new job', 'translated_title2': "New Year, New Resolution-Tips to Help Achieve This Year's Goal"}
-------------- 18 --------------
{'pair_id': '1484188930_1484152024', 'url1_lang': 'en', 'google_lang1': 'en', 'url2_lang': 'en', 'google_lang2': 'en', 'title1': '10 New Year’s Gaming Resolution Suggestions for 2020', 'title2': 'Local gyms see spike in memberships due to fitness resolutions', 'translated_title1': '10 New Year’s Gaming Resolution Suggestions for 2020', 'translated_title2': 'Local gyms see spike in memberships due to fitness resolutions'}
-------------- 19 --------------
{'pair_id': '1484699049_1484327278', 'url1_lang':

...

C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat in

-------------- 4878 --------------
{'pair_id': '1534704977_1533440008', 'url1_lang': 'zh', 'google_lang1': 'zh-CN', 'url2_lang': 'zh', 'google_lang2': 'zh-CN', 'title1': '【地评线】江右时评：联防联控防反弹 同舟共济战疫情', 'title2': '【地评线】红辣椒网评：疫情防控这根弦只能绷紧不能放松', 'translated_title1': '[Review line] Jiang Right Times: Lian Defense Control Defensive Swong Tongzhou Tongji Epide', 'translated_title2': '[Review line] Red hot pepper net review: Epidemic prevention and control This string can only be tightened to relax'}
-------------- 4879 --------------
{'pair_id': '1511135586_1512529082', 'url1_lang': 'zh', 'google_lang1': 'zh-CN', 'url2_lang': 'zh', 'google_lang2': 'zh-CN', 'title1': '托卡耶夫总统致信中国国家主席习近平', 'title2': '吉尔吉斯坦总统就从武汉撤回侨民一事向哈萨克斯坦表示感谢', 'translated_title1': 'President Tosayev sent a letter to China President Xi Jinping', 'translated_title2': 'President Kyrgyzstan expressed his gratitude to Kazakhstan from the withdrawal of Wuhan withdraw between Wuhan.'}
-------------- 4880 --------------
{'pair_id': '149

C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat in

-------------- 4888 --------------
{'pair_id': '1536343918_1534950960', 'url1_lang': 'es', 'google_lang1': 'es', 'url2_lang': 'it', 'google_lang2': 'it', 'title1': 'Coronavirus en EEUU deja por ahora dos muertos; Trump dice que todo está “bajo control”', 'title2': 'Coronavirus, Trump “Controlli per chi viaggia dall’Italia”', 'translated_title1': 'Coronavirus in the US leaves for two dead;Trump says that everything is "under control"', 'translated_title2': 'Coronavirus, Trump "Controls for those traveling from Italy"'}
-------------- 4889 --------------
{'pair_id': '1587323264_1588806881', 'url1_lang': 'es', 'google_lang1': 'es', 'url2_lang': 'it', 'google_lang2': 'it', 'title1': 'Tom Hanks le mandó un regalo a niño australiano acosado por llamarse “Corona”', 'title2': "Australia, bimbo bullizzato per il nome Corona, Tom Hanks: 'Hai un amico in me'", 'translated_title1': 'Tom Hanks sent him a gift to Australian child harassed by calling "Crown"', 'translated_title2': "Australia, Baby Bu

C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_title_df = new_title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\1335813852.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat in

In [61]:
new_title_df.iloc[2941]

pair_id                                          1630809649_1537380831
url1_lang                                                           tr
google_lang1                                                        tr
url2_lang                                                           tr
google_lang2                                                        tr
title1               Atalay Demirci'ye hapis cezasının gerekçeli ka...
title2               Komedyen Atalay Demirci FETÖ'den aldığı ceza b...
translated_title1    Atalay Demirci's reasoned decision of imprison...
translated_title2    The penalty taken from the Comedyen Atalay Bla...
Name: 2941, dtype: object

In [62]:
path = 'eval/_EVAL_title_translated.csv'
new_title_df.to_csv(path,index=False)  



### Embedding and cosine similarity

A pre-trained model (BERT) is used to embed the translated titles. The documentation of the used language model can be found at [SentenceTransformer](https://www.sbert.net/docs/package_reference/SentenceTransformer.html). <br><br>

After that, cosine similarity is applied by using the SKLearn package. The documentation can be found at [Cosine Similarity](https://scikit-learn.org/stable/modules/generated/sklearn.metrics.pairwise.cosine_similarity.html).

In [63]:
title_cos_sim_df = pd.DataFrame(columns = ["pair_id","url1_lang", "google_lang1","url2_lang","google_lang2", "id1","id2","title1","title2","translated_title1","translated_title2","cos_sim"])

for i, row in new_title_df.iterrows():
    cos_sim = 0
    sentences = [
        str(row['translated_title1']),
        str(row['translated_title2']),
    ]

    sentence_embeddings = model.encode(sentences)

    cs = cosine_similarity(
        [sentence_embeddings[0]],
        sentence_embeddings[1:]
    )
    cos_sim = cs[0][0]
    pair = row['pair_id']
    print('--------------',i,'---------------')
    print(pair)
    for s in sentences:
        print(s)
    print('cos_sim: ',cos_sim)
    
    
    entry = {"pair_id": pair, "url1_lang":row['url1_lang'],"google_lang1":row['google_lang1'],"url2_lang":row['url2_lang'],"google_lang2":row['google_lang2'],"title1":row["title1"],"title2":row["title2"],"translated_title1":row['translated_title1'],"translated_title2":row['translated_title2'],"cos_sim":cos_sim}
    title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)



-------------- 0 ---------------
1484189203_1484121193
Police: 2 men stole tools from Lowe’s in Davie
No-swim advisory lifted for Deerfield Beach Pier
cos_sim:  0.21453756
-------------- 1 ---------------
1484011097_1484011106
Open database leaked 179GB in customer, US government, and military records
Best Western’s Massive Data Leak: 179GB Amazon Database Open to All
cos_sim:  0.63478005


C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\2019597359.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\2019597359.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\2019597359.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)


-------------- 2 ---------------
1484039488_1484261803
Ducks are own worst enemies in sloppy loss in Las Vegas
Woody Guthrie's 1943 New Year's Resolutions are a powerful reminder to "Keep the hope machine running."
cos_sim:  0.24085885
-------------- 3 ---------------
1484332324_1484796748
Another Bengal vs Centre tussle? Govt rejects state’s Republic Day tableau proposal
'Congress Rejected 7 Times': BJP's Reminder as Row Over Bengal, Maharashtra R-Day Tableau Continues
cos_sim:  0.65150106


C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\2019597359.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\2019597359.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\2019597359.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)


-------------- 4 ---------------
1484012256_1484419682
Bars and clubs you loved and lost this decade in Brum
Top 20 films of the 2010s
cos_sim:  0.367649
-------------- 5 ---------------
1484188974_1484299664
How to free up iCloud storage space
Leading and managing organisational change
cos_sim:  0.49190444
-------------- 6 ---------------
1484703270_1484167784
Op Ed: Losing Sheila’s Smile
Gov. Tony Evers says relationship with Republican leaders 'could be better'
cos_sim:  0.3511644


...

 ---------------
1529909197_1529885148
Weinstein, guilty of two sexual crimes in historical trial for methoo
Harassment: Weinstein guilty of sexual violence and rape
cos_sim:  0.7722106
-------------- 4897 ---------------
1553907621_1553488848
Denver Nuggets reports that "a member of the organization" contracted Coronavirus
Coronavirus, a case also among the Denver Nuggets
cos_sim:  0.7824235
-------------- 4898 ---------------
1646957948_1643667075


C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\2019597359.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\2019597359.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\2019597359.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)


Living in Spain is cheaper than in the European average
Coronavirus, in Europe 140 thousand dead in March-April
cos_sim:  0.26059526
-------------- 4899 ---------------
1504063453_1502866628
Activate epidemiological surveillance system in Venezuelan ports and airports - El Aragueño
Coronavirus in China: consumption of snakes and bat soup between the transmission causes
cos_sim:  0.38693175
-------------- 4900 ---------------
1647862428_1647712939
Emite Iran Arrest Order against Tump by General Soleimani murder
Iran emits stop mandate for trump for the murder of sunimani
cos_sim:  0.8506143


C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\2019597359.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\2019597359.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_27824\2019597359.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)


-------------- 4901 ---------------
1636570015_1637492652
Biden, with more than 10 points that Trump in key states of Florida and Michigan
USA 2020 survey: Biden ahead in the 6 states in the balance
cos_sim:  0.43187153


In [64]:
title_cos_sim_df

pair_id url1_lang google_lang1 url2_lang google_lang2  \
0     1484189203_1484121193        en           en        en           en   
1     1484011097_1484011106        en           en        en           en   
2     1484039488_1484261803        en           en        en           en   
3     1484332324_1484796748        en           en        en           en   
4     1484012256_1484419682        en           en        en           en   
...                     ...       ...          ...       ...          ...   
4897  1553907621_1553488848        es           es        it           it   
4898  1646957948_1643667075        es           es        it           it   
4899  1504063453_1502866628        es           es        it           it   
4900  1647862428_1647712939        es           es        it           it   
4901  1636570015_1637492652        es           es        it           it   

      id1  id2                                             title1  \
0     NaN  NaN     Police: 2 men stole tools from Lowe’s in Davie   
1     NaN  NaN  Open database leaked 179GB in customer, US gov...   
2     NaN  NaN  Ducks are own worst enemies in sloppy loss in ...   
3     NaN  NaN  Another Bengal vs Centre tussle? Govt rejects ...   
4     NaN  NaN  Bars and clubs you loved and lost this decade ...   
...   ...  ...                                                ...   
4897  NaN  NaN  Denver Nuggets reporta que “un miembro de la o...   
4898  NaN  NaN  Vivir en España es más barato que en la media ...   
4899  NaN  NaN  Activan sistema de vigilancia epidemiológica e...   
4900  NaN  NaN  Emite Irán orden de arresto contra Tump por as...   
4901  NaN  NaN  Biden, con más de 10 puntos que Trump en estad...   

                                                 title2  \
0      No-swim advisory lifted for Deerfield Beach Pier   
1     Best Western’s Massive Data Leak: 179GB Amazon...   
2     Woody Guthrie's 1943 New Year's Resolutions ar...   
3     'Congress Rejected 7 Times': BJP's Reminder as...   
4                             Top 20 films of the 2010s   
...                                                 ...   
4897    Coronavirus, un caso anche fra i Denver Nuggets   
4898  Coronavirus, in Europa 140mila morti in più in...   
4899  Coronavirus in Cina: consumo di serpenti e zup...   
4900  Iran emette mandato di arresto per Trump per l...   
4901  Sondaggio Usa 2020: Biden in vantaggio nei 6 S...   

                                      translated_title1  \
0        Police: 2 men stole tools from Lowe’s in Davie   
1     Open database leaked 179GB in customer, US gov...   
2     Ducks are own worst enemies in sloppy loss in ...   
3     Another Bengal vs Centre tussle? Govt rejects ...   
4     Bars and clubs you loved and lost this decade ...   
...                                                 ...   
4897  Denver Nuggets reports that "a member of the o...   
4898  Living in Spain is cheaper than in the Europea...   
4899  Activate epidemiological surveillance system i...   
4900  Emite Iran Arrest Order against Tump by Genera...   
4901  Biden, with more than 10 points that Trump in ...   

                                      translated_title2   cos_sim  
0      No-swim advisory lifted for Deerfield Beach Pier  0.214538  
1     Best Western’s Massive Data Leak: 179GB Amazon...   0.63478  
2     Woody Guthrie's 1943 New Year's Resolutions ar...  0.240859  
3     'Congress Rejected 7 Times': BJP's Reminder as...  0.651501  
4                             Top 20 films of the 2010s  0.367649  
...                                                 ...       ...  
4897  Coronavirus, a case also among the Denver Nuggets  0.782423  
4898  Coronavirus, in Europe 140 thousand dead in Ma...  0.260595  
4899  Coronavirus in China: consumption of snakes an...  0.386932  
4900  Iran emits stop mandate for trump for the murd...  0.850614  
4901  USA 2020 survey: Biden ahead in the 6 states i...  0.431872  

[4902 rows x 12 columns]

In [65]:
path = 'eval/_EVAL_title_cosSim_score.csv'
title_cos_sim_df.to_csv(path,index=False)

### Compare title cosine similarity score<br>

We compare the annotated overall score of pairs with the similarity score obtained by 
cosine similarity on titles of articles. <br><br>

This comparison is analogous to the one in the case of the training dataset, however, in principle, this step is not relevant for the final evaluation of our solution. This comparison can be thought as a double check to make sure that the choice of features makes sense and is motivated by curiosity rather then necessity.

In [12]:
# get a dataframe showing the distribution of label (annotated overall similarity) and our title (NAMED ENTITY?) similarity score
import math
eval_df = pd.read_csv ('eval/_EVAL_details_in_df.csv')

def normal_round(n):
    if n - math.floor(n) < 0.5:
        return int(math.floor(n))
    return int(math.ceil(n))

compare_df = pd.DataFrame(columns = ["overall","title_cos_sim"])


for i, row in eval_df.iterrows(): 
    # just to check if dataframes align
    if row["pair_id"] != row['pair_id']:
        print('---------------------',i,'-----------------------')
        print(row["pair_id"])
        
    print('---------------------',i,'-----------------------')
    label = normal_round(float(row['Overall']))
    print('label:',label)
    score = eval_translated.iloc[i]['cos_sim']
    print('score:',score)
    
    
    entry = {"overall":label,"title_cos_sim":score}
    compare_df = compare_df.append(entry, ignore_index = True)


--------------------- 0 -----------------------
label: 4
score: 0.21453748643398285
--------------------- 1 -----------------------
label: 1
score: 0.6347798705101013
--------------------- 2 -----------------------
label: 4
score: 0.24085868895053864
--------------------- 3 -----------------------
label: 2
score: 0.6515008211135864
--------------------- 4 -----------------------
label: 4
score: 0.36764878034591675
--------------------- 5 -----------------------
label: 4
score: 0.49190449714660645
--------------------- 6 -----------------------
label: 3
score: 0.35116416215896606
--------------------- 7 -----------------------
label: 3
score: 0.28449809551239014
--------------------- 8 -----------------------
label: 2
score: 0.6909687519073486
--------------------- 9 -----------------------
label: 4
score: 0.3899672031402588
--------------------- 10 -----------------------
label: 4
score: 0.11088698357343674
--------------------- 11 -----------------------
label: 3
score: 0.572531700134

--------------------- 112 -----------------------
label: 4
score: 0.426266610622406
--------------------- 113 -----------------------
label: 2
score: 0.9662722945213318
--------------------- 114 -----------------------
label: 4
score: 0.14823149144649506
--------------------- 115 -----------------------
label: 4
score: 0.753546953201294
--------------------- 116 -----------------------
label: 1
score: 0.8367294073104858
--------------------- 117 -----------------------
label: 1
score: 0.6265904307365417
--------------------- 118 -----------------------
label: 1
score: 0.2727872133255005
--------------------- 119 -----------------------
label: 1
score: 0.5728503465652466
--------------------- 120 -----------------------
label: 1
score: 0.7444695234298706
--------------------- 121 -----------------------
label: 4
score: 0.5995566844940186
--------------------- 122 -----------------------
label: 2
score: 0.5476468801498413
--------------------- 123 -----------------------
label: 1
score: 

--------------------- 276 -----------------------
label: 4
score: 0.38419264554977417
--------------------- 277 -----------------------
label: 3
score: 0.7467191219329834
--------------------- 278 -----------------------
label: 3
score: 0.32397136092185974
--------------------- 279 -----------------------
label: 3
score: 0.17200632393360138
--------------------- 280 -----------------------
label: 1
score: 0.5304293036460876
--------------------- 281 -----------------------
label: 3
score: 0.30065780878067017
--------------------- 282 -----------------------
label: 3
score: 0.2612842321395874
--------------------- 283 -----------------------
label: 3
score: 0.581809937953949
--------------------- 284 -----------------------
label: 1
score: 0.3411259949207306
--------------------- 285 -----------------------
label: 4
score: 0.27876248955726624
--------------------- 286 -----------------------
label: 4
score: 0.44229525327682495
--------------------- 287 -----------------------
label: 3
s

--------------------- 399 -----------------------
label: 4
score: 0.5680216550827026
--------------------- 400 -----------------------
label: 3
score: 0.5194289684295654
--------------------- 401 -----------------------
label: 4
score: 0.1968376785516739
--------------------- 402 -----------------------
label: 2
score: 0.7800809144973755
--------------------- 403 -----------------------
label: 1
score: 0.4234757721424103
--------------------- 404 -----------------------
label: 2
score: 0.7016919851303101
--------------------- 405 -----------------------
label: 2
score: 0.414588987827301
--------------------- 406 -----------------------
label: 3
score: 0.5252431035041809
--------------------- 407 -----------------------
label: 1
score: 0.35156333446502686
--------------------- 408 -----------------------
label: 4
score: 0.35755103826522827
--------------------- 409 -----------------------
label: 4
score: 0.3963874280452728
--------------------- 410 -----------------------
label: 4
score

--------------------- 576 -----------------------
label: 3
score: 0.484933078289032
--------------------- 577 -----------------------
label: 2
score: 0.6623413562774658
--------------------- 578 -----------------------
label: 3
score: 0.6169600486755371
--------------------- 579 -----------------------
label: 1
score: 0.718527615070343
--------------------- 580 -----------------------
label: 3
score: 0.20186856389045715
--------------------- 581 -----------------------
label: 2
score: 0.520972490310669
--------------------- 582 -----------------------
label: 4
score: 0.4696214497089386
--------------------- 583 -----------------------
label: 2
score: 0.507270336151123
--------------------- 584 -----------------------
label: 4
score: 0.15578287839889526
--------------------- 585 -----------------------
label: 4
score: 0.7680490612983704
--------------------- 586 -----------------------
label: 4
score: 0.3894743323326111
--------------------- 587 -----------------------
label: 4
score: 0

...

--------------------- 4134 -----------------------
label: 1
score: 0.7922772169113159
--------------------- 4135 -----------------------
label: 1
score: 0.9224567413330078
--------------------- 4136 -----------------------
label: 2
score: 0.6255367994308472
--------------------- 4137 -----------------------
label: 2
score: 0.9883161783218384
--------------------- 4138 -----------------------
label: 4
score: 0.5542638897895813
--------------------- 4139 -----------------------
label: 1
score: 0.23693665862083435
--------------------- 4140 -----------------------
label: 3
score: 0.46494048833847046
--------------------- 4141 -----------------------
label: 2
score: 0.5070028305053711
--------------------- 4142 -----------------------
label: 1
score: 0.5844565629959106
--------------------- 4143 -----------------------
label: 2
score: 0.6262416839599609
--------------------- 4144 -----------------------
label: 1
score: 0.8921559453010559
--------------------- 4145 -----------------------
l

--------------------- 4337 -----------------------
label: 1
score: 0.8355913758277893
--------------------- 4338 -----------------------
label: 2
score: 0.40904778242111206
--------------------- 4339 -----------------------
label: 1
score: 0.40281736850738525
--------------------- 4340 -----------------------
label: 1
score: 0.4556361436843872
--------------------- 4341 -----------------------
label: 4
score: 0.6048130989074707
--------------------- 4342 -----------------------
label: 2
score: 0.2108759582042694
--------------------- 4343 -----------------------
label: 1
score: 0.8260681629180908
--------------------- 4344 -----------------------
label: 1
score: 0.9081646203994751
--------------------- 4345 -----------------------
label: 1
score: 0.40788036584854126
--------------------- 4346 -----------------------
label: 1
score: 0.3841535449028015
--------------------- 4347 -----------------------
label: 1
score: 0.912469208240509
--------------------- 4348 -----------------------
l

--------------------- 4510 -----------------------
label: 1
score: 0.6252447962760925
--------------------- 4511 -----------------------
label: 2
score: 0.40090131759643555
--------------------- 4512 -----------------------
label: 2
score: 0.6669336557388306
--------------------- 4513 -----------------------
label: 1
score: 0.5970234870910645
--------------------- 4514 -----------------------
label: 1
score: 0.9956134557723999
--------------------- 4515 -----------------------
label: 1
score: 0.416200190782547
--------------------- 4516 -----------------------
label: 3
score: 0.4866587817668915
--------------------- 4517 -----------------------
label: 1
score: 0.930750846862793
--------------------- 4518 -----------------------
label: 2
score: 0.38850411772727966
--------------------- 4519 -----------------------
label: 1
score: 0.8089622855186462
--------------------- 4520 -----------------------
label: 4
score: 0.3078521192073822
--------------------- 4521 -----------------------
lab

--------------------- 4688 -----------------------
label: 1
score: 0.5141658782958984
--------------------- 4689 -----------------------
label: 2
score: 0.6934480667114258
--------------------- 4690 -----------------------
label: 2
score: 0.6961842775344849
--------------------- 4691 -----------------------
label: 1
score: 0.7255733013153076
--------------------- 4692 -----------------------
label: 2
score: 0.6037602424621582
--------------------- 4693 -----------------------
label: 1
score: 0.918237566947937
--------------------- 4694 -----------------------
label: 1
score: 0.7801847457885742
--------------------- 4695 -----------------------
label: 1
score: 0.46456384658813477
--------------------- 4696 -----------------------
label: 1
score: 0.8666020035743713
--------------------- 4697 -----------------------
label: 1
score: 0.7325971126556396
--------------------- 4698 -----------------------
label: 1
score: 0.9695076942443848
--------------------- 4699 -----------------------
lab

--------------------- 4849 -----------------------
label: 1
score: 0.7760738730430603
--------------------- 4850 -----------------------
label: 2
score: 0.7726746797561646
--------------------- 4851 -----------------------
label: 3
score: 0.5491670370101929
--------------------- 4852 -----------------------
label: 1
score: 0.9587469100952148
--------------------- 4853 -----------------------
label: 4
score: 0.4919368624687195
--------------------- 4854 -----------------------
label: 1
score: 0.7426186800003052
--------------------- 4855 -----------------------
label: 3
score: 0.3871762454509735
--------------------- 4856 -----------------------
label: 2
score: 0.5821981430053711
--------------------- 4857 -----------------------
label: 1
score: 0.7153617143630981
--------------------- 4858 -----------------------
label: 1
score: 0.4598797559738159
--------------------- 4859 -----------------------
label: 2
score: 0.6569216847419739
--------------------- 4860 -----------------------
lab

In [13]:

compare_4 = compare_df[compare_df['overall']==4.0]
compare_3 = compare_df[compare_df['overall']==3.0]
compare_2 = compare_df[compare_df['overall']==2.0]
compare_1 = compare_df[compare_df['overall']==1.0]
len(compare_df)
len(compare_4) + len(compare_3) + len(compare_2) +len(compare_1)

i_list = [1.0,2.0,3.0,4.0]
compare = [compare_1,compare_2,compare_3,compare_4]
col = 'title_cos_sim'
for i in i_list:
    index = int(i)-1
    c = compare[index]
    print('Number of pairs that are rated as ',i,':')
    print(len(c))
    print('Pairs that are rated as ',i,', title named entity score is 0: (value, percentage)')
    print(len(c[c[col]==0]), ', ', len(c[c[col]==0])/len(c)*100,'%')
    print('Pairs that are rated as ',i,', title named entity score is > 0.3:')
    print(len(c[c[col]>0.3]), ', ', len(c[c[col]>0.3])/len(c)*100,'%')
    print('Pairs that are rated as ',i,', title named entity score is > 0.5:')
    print(len(c[c[col]>0.5]), ', ', len(c[c[col]>0.5])/len(c)*100,'%')
    print('Pairs that are rated as ',i,', title named entity score is 1.0:')
    print(len(c[c[col]==1.0]), ', ', len(c[c[col]==1.0])/len(c)*100,'%')
    

Number of pairs that are rated as  1.0 :
1443
Pairs that are rated as  1.0 , title named entity score is 0: (value, percentage)
0 ,  0.0 %
Pairs that are rated as  1.0 , title named entity score is > 0.3:
1395 ,  96.67359667359668 %
Pairs that are rated as  1.0 , title named entity score is > 0.5:
1136 ,  78.72487872487872 %
Pairs that are rated as  1.0 , title named entity score is 1.0:
3 ,  0.2079002079002079 %
Number of pairs that are rated as  2.0 :
1124
Pairs that are rated as  2.0 , title named entity score is 0: (value, percentage)
0 ,  0.0 %
Pairs that are rated as  2.0 , title named entity score is > 0.3:
1035 ,  92.08185053380782 %
Pairs that are rated as  2.0 , title named entity score is > 0.5:
734 ,  65.30249110320284 %
Pairs that are rated as  2.0 , title named entity score is 1.0:
0 ,  0.0 %
Number of pairs that are rated as  3.0 :
959
Pairs that are rated as  3.0 , title named entity score is 0: (value, percentage)
0 ,  0.0 %
Pairs that are rated as  3.0 , title named e


### Remarks: <br>

We notice that using cosine similarity for measuring similarity seems to be consistent with the annotated similarity score. This can be seen, for instance by noticing that in the case of very similar articles (scored 1.0) the percentage of the ones that have less than 0.3 similarity score is around 3%, on the other hand, for very dissimilar articles (scored 4.0), the percentage of the ones that have less than 0.3 similarity score is 25%.